In [1]:
import os
import json
import pickle
import pandas as pd
import numpy as np
from sklearn.linear_model import RidgeCV, LogisticRegressionCV
from sklearn.model_selection import StratifiedKFold, cross_val_score
from tqdm.notebook import tqdm
from rca import make_binary_scoring, make_multiclass_scoring, process_categorical, best_logistic_solver, checker

## Loading Data

We drop feature_overlap because it contains many NaNs and compo_attribs because it doesn't have a large enough vocabulary and is also a identical to a 65 of the norms in the psychNorms dataset.

In [2]:
with open('../../data/brain_behav_union.pkl', 'rb') as f:
    brain_behav_union = pickle.load(f)

# Loading dictionary of dtype to embed
with open('../../data/dtype_to_embed.json', 'r') as f:
    dtype_to_embed = json.load(f)
    
brain_behav_names = dtype_to_embed['brain'] + dtype_to_embed['behavior']

# Pulling and standardising embeddings
embeds = {}
embeds_path = '../../data/embeds/'
for f_name in tqdm(os.listdir(embeds_path)):
    if f_name not in ['feature_overlap.csv', 'compo_attribs.csv']:  # dropping since contains many NaNs
        
        embed = pd.read_csv(embeds_path + f_name, index_col=0)
        embed_name = f_name.split('.')[0]
        
        # Subsetting to brain and behavior vocab
        embed = embed.loc[embed.index.intersection(brain_behav_union)]
        
        # Standardising
        embeds[embed_name] = (embed - embed.mean()) / embed.std()

{name: embed.shape for name, embed in embeds.items()}

  0%|          | 0/26 [00:00<?, ?it/s]

{'CBOW_GoogleNews': (42830, 300),
 'PPMI_SVD_SouthFlorida': (4959, 300),
 'SVD_sim_rel': (6002, 300),
 'spherical_text_Wikipedia': (35533, 300),
 'norms_sensorimotor': (36854, 11),
 'fastText_Wiki_News': (43143, 300),
 'PPMI_SVD_EAT': (7775, 300),
 'GloVe_Twitter': (32947, 200),
 'LexVec_CommonCrawl': (44082, 300),
 'fastTextSub_OpenSub': (40607, 300),
 'eye_tracking': (7486, 6),
 'SGSoftMaxOutput_SWOW': (25442, 300),
 'morphoNLM': (32769, 50),
 'SGSoftMaxInput_SWOW': (11783, 300),
 'fMRI_text_hyper_align': (1205, 1000),
 'GloVe_Wikipedia': (39421, 300),
 'EEG_text': (3355, 104),
 'fastText_CommonCrawl': (44443, 300),
 'fMRI_speech_hyper_align': (579, 6),
 'PPMI_SVD_SWOW': (11783, 300),
 'microarray': (626, 15),
 'EEG_speech': (1591, 130),
 'GloVe_CommonCrawl': (44278, 300),
 'THINGS': (1562, 49)}

In [3]:
with open('../../data/embed_to_dtype.json', 'r') as f:
    embed_to_type = json.load(f)
embed_to_type

{'CBOW_GoogleNews': 'text',
 'fastText_CommonCrawl': 'text',
 'fastText_Wiki_News': 'text',
 'fastTextSub_OpenSub': 'text',
 'GloVe_CommonCrawl': 'text',
 'GloVe_Twitter': 'text',
 'GloVe_Wikipedia': 'text',
 'LexVec_CommonCrawl': 'text',
 'morphoNLM': 'text',
 'spherical_text_Wikipedia': 'text',
 'eye_tracking': 'brain',
 'EEG_speech': 'brain',
 'EEG_text': 'brain',
 'fMRI_speech_hyper_align': 'brain',
 'fMRI_text_hyper_align': 'brain',
 'microarray': 'brain',
 'PPMI_SVD_SWOW': 'behavior',
 'SGSoftMaxInput_SWOW': 'behavior',
 'SGSoftMaxOutput_SWOW': 'behavior',
 'PPMI_SVD_SouthFlorida': 'behavior',
 'PPMI_SVD_EAT': 'behavior',
 'THINGS': 'behavior',
 'feature_overlap': 'behavior',
 'norms_sensorimotor': 'behavior',
 'compo_attribs': 'behavior',
 'SVD_sim_rel': 'behavior'}

In [4]:
# Loading norms
norms = pd.read_csv('../../data/psychNorms/psychNorms_processed.zip', index_col=0, compression='zip', low_memory=False)
norm_meta = pd.read_csv('../../data/psychNorms/psychNorms_metadata_processed.csv', index_col='norm')
norms

frequency_lund  frequency_kucera  frequency_subtlexus  \
word                                                                 
'em                     0.0               NaN                  NaN   
'neath                  0.0               NaN                  NaN   
're                     0.0               NaN                  NaN   
'shun                   0.0               NaN                  NaN   
'tis                    0.0               NaN                  NaN   
...                     ...               ...                  ...   
shrick                  NaN               NaN                  NaN   
post office             NaN               NaN                  NaN   
fishing rod             NaN               NaN                  NaN   
March                   NaN               NaN                  NaN   
May                     NaN               NaN                  NaN   

             frequency_subtlexuk  frequency_blog_gimenes  \
word                                                       
'em                          NaN                     NaN   
'neath                       NaN                     NaN   
're                          NaN                     NaN   
'shun                        NaN                     NaN   
'tis                         NaN                     NaN   
...                          ...                     ...   
shrick                       NaN                     NaN   
post office                  NaN                     NaN   
fishing rod                  NaN                     NaN   
March                        NaN                     NaN   
May                          NaN                     NaN   

             frequency_twitter_gimenes  frequency_news_gimenes  \
word                                                             
'em                                NaN                     NaN   
'neath                             NaN                     NaN   
're                                NaN                     NaN   
'shun                              NaN                     NaN   
'tis                               NaN                     NaN   
...                                ...                     ...   
shrick                             NaN                     NaN   
post office                        NaN                     NaN   
fishing rod                        NaN                     NaN   
March                              NaN                     NaN   
May                                NaN                     NaN   

             frequency_written_cobuild  frequency_spoken_cobuild  \
word                                                               
'em                             1.3617                    1.9138   
'neath                          0.0000                    0.0000   
're                             0.9031                    1.6335   
'shun                           0.0000                    0.0000   
'tis                            0.4771                    0.6021   
...                                ...                       ...   
shrick                             NaN                       NaN   
post office                        NaN                       NaN   
fishing rod                        NaN                       NaN   
March                              NaN                       NaN   
May                                NaN                       NaN   

             context_diversity_subtlexus  ...  person_vanarsdall  \
word                                      ...                      
'em                                  NaN  ...                NaN   
'neath                               NaN  ...                NaN   
're                                  NaN  ...                NaN   
'shun                                NaN  ...                NaN   
'tis                                 NaN  ...                NaN   
...                                  ...  ...                ...   
shrick                           

## Cross Validation

In [5]:
# Ridge
min_ord, max_ord = -5, 5
alphas = np.logspace(
    min_ord, max_ord, max_ord - min_ord + 1
)
ridge = RidgeCV(alphas=alphas)

# Logistic hyperparameters
Cs = 1 / alphas
inner_cv = 5
penalty = 'l2'

# Scorers
binary_scoring = make_binary_scoring()
multiclass_scoring = make_multiclass_scoring()
continuous_scoring = 'r2'

# outer_cv setting 
outer_cv, n_jobs = 5, 10

# RCA
rca = []
for embed_name in tqdm(embeds.keys()):
    embed = embeds[embed_name]
    
    to_print = []
    for norm_name in tqdm(norms.columns, desc=embed_name):
        
        # Aligning data
        y = norms[norm_name].dropna()
        X, y = embed.align(y, axis=0, join='inner', copy=True) 
        
        # Checking norm dtype 
        norm_dtype = norm_meta.loc[norm_name, 'type']
        
        # Solvers, scoring, estimators
        if norm_dtype in ['binary', 'multiclass']:
            X, y = process_categorical(outer_cv, inner_cv, X, y)
            
            # may have switched form multi to bin after processing
            norm_dtype = 'binary' if len(y.unique()) == 2 else 'multiclass'
            
            # Cross validation settings for logistic regression
            solver = best_logistic_solver(X, norm_dtype)
            
            # Defining logistic regression 
            estimator = LogisticRegressionCV(
                Cs=Cs, penalty=penalty, cv=StratifiedKFold(inner_cv),
                solver=solver, n_jobs=8
            )
            scoring = binary_scoring if norm_dtype == 'binary' else multiclass_scoring
        else: # continuous
            estimator, scoring = ridge, continuous_scoring
  
        # Cross validation
        associated_embed = norm_meta.loc[norm_name, 'associated_embed']
        check = checker(embed_name, y, norm_dtype, associated_embed, outer_cv)
        if check == 'pass':
            r2s = cross_val_score(estimator, X, y, cv=outer_cv, scoring=scoring, n_jobs=n_jobs) # stratification is automatically used for classification
            r2_mean, r2_sd = r2s.mean(), r2s.std()
        else:
            r2_mean, r2_sd = np.nan, np.nan
            
        # Saving
        train_n = int(((outer_cv - 1) / outer_cv) * len(X))
        test_n = len(X) - train_n
        p = X.shape[1]
        embed_type = embed_to_type[embed_name]
        rca.append([
            embed_name, embed_type, norm_name, train_n, test_n, p, 
            r2_mean, r2_sd, check
        ])
        
        to_print.append([norm_name, train_n, r2_mean, r2_sd, check])
            
            
    to_print = pd.DataFrame(to_print, columns=['norm' , 'train_n', 'r2_mean', 'r2_sd', 'check'])
    print(to_print.sort_values('r2_mean', ascending=False).head(10))

rca = pd.DataFrame(
    rca, columns=[
        'embed', 'embed_type', 'norm', 'train_n', 'test_n', 'p', 
        'r2_mean', 'r2_sd', 'check'
    ]
)

rca.to_csv('../../data/results/rca.csv', index=False)
rca

  0%|          | 0/24 [00:00<?, ?it/s]

CBOW_GoogleNews:   0%|          | 0/291 [00:00<?, ?it/s]

/datapool-1/homepoint/zhussain/anaconda3/envs/psychProbing/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/envs/psychProbing/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/envs/psychProbing/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/envs/psychProbing/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/envs/psychProbing/lib/python3.10/site-packages/sklearn/linear_model

                        norm  train_n   r2_mean     r2_sd check
281        person_vanarsdall      960  0.817393  0.019020  pass
279       thought_vanarsdall      960  0.815265  0.013993  pass
216            valence_britz      375  0.809409  0.024288  pass
217         social_des_britz      375  0.805828  0.022057  pass
282         goals_vanarsdall      960  0.796573  0.020816  pass
161          goals_wilkowski      837  0.785734  0.012998  pass
176      concreteness_hollis      828  0.784008  0.018515  pass
24      concreteness_glasgow     3672  0.781250  0.009689  pass
267     likableness_anderson      386  0.780283  0.036849  pass
280  reproduction_vanarsdall      960  0.776169  0.009854  pass


PPMI_SVD_SouthFlorida:   0%|          | 0/291 [00:00<?, ?it/s]

...

                      norm  train_n   r2_mean     r2_sd check
216          valence_britz      384  0.832397  0.096434  pass
217       social_des_britz      384  0.827537  0.084828  pass
281      person_vanarsdall      960  0.818899  0.027482  pass
279     thought_vanarsdall      960  0.813102  0.019946  pass
282       goals_vanarsdall      960  0.806998  0.021245  pass
211  tabooness_janschewitz      359  0.793416  0.050916  pass
267   likableness_anderson      405  0.773479  0.090871  pass
161        goals_wilkowski      842  0.762251  0.087604  pass
253   likableness_chandler      644  0.755676  0.083720  pass
174         valence_hollis      829  0.755092  0.072602  pass


THINGS:   0%|          | 0/291 [00:00<?, ?it/s]

/datapool-1/homepoint/zhussain/anaconda3/envs/psychProbing/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/envs/psychProbing/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/envs/psychProbing/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/envs/psychProbing/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/envs/psychProbing/lib/python3.10/site-packages/sklearn/linear_model

                        norm  train_n   r2_mean     r2_sd check
104         biomotion_binder      128  0.872332  0.042505  pass
278        living_vanarsdall      376  0.841733  0.019199  pass
110              body_binder      128  0.834058  0.052231  pass
280  reproduction_vanarsdall      376  0.827012  0.027135  pass
35       gustatory_lancaster     1235  0.813969  0.040591  pass
123             taste_binder      128  0.809113  0.100118  pass
121             music_binder      128  0.760995  0.067979  pass
283      movement_vanarsdall      376  0.723601  0.033689  pass
279       thought_vanarsdall      376  0.721569  0.080251  pass
130              path_binder      128  0.715336  0.068376  pass


ValueError: 8 columns passed, passed data had 9 columns